## Loading Dataset

In [1]:
import numpy as np
import pandas as pd

In [2]:
X_fn = "./data/combine_astii_astiii_filter_all_smoothing_ipm_K_pneumonia_norm.npy"
y_fn = "./data/y_astii_astiii_filter_all_ipm_K_pneumonia.npy"
patient_fn = "./data/patient_astii_astiii_filter_all_ipm_K_pneumonia.npy"
X_train_raw = np.load(X_fn,allow_pickle=True)
y_train_raw = np.load(y_fn,allow_pickle=True)
patient_train_raw = np.load(patient_fn,allow_pickle=True)

classnames=['CR K_pneumonia','CS K_pneumonia']


df_p = pd.DataFrame(X_train_raw)
df_p['Classes'] = y_train_raw
df_p['Patient_ID'] = patient_train_raw 


In [3]:
if not isinstance(X_train_raw, np.ndarray):
    X_train_raw = np.array(X_train_raw, dtype=np.float32)
elif X_train_raw.dtype != np.float32:
    X_train_raw = X_train_raw.astype(np.float32)

### Model Setting

In [4]:
# model
from model import Variant_LeNet,ResNet,RamanNet,ViT
from tqdm import tqdm
import torch
import pandas as pd
import torch.nn as nn
from torch.autograd import Variable
from losses import FocalLoss
from losses import AdaptiveProxyAnchorLoss
from imblearn.metrics import specificity_score
from sklearn.metrics import (
    confusion_matrix,
    accuracy_score,
    precision_score,
    recall_score,
    f1_score,
    auc,
    roc_curve,
)
from pytorchtools import EarlyStopping
import torch.optim as optim
# Plot
from plot import plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve, plot_heatmap,plot_tsne_interactive_html
import matplotlib.pyplot as plt

import seaborn as sns
from sklearn.metrics import confusion_matrix
from config import ORDER, STRAINS
import math

# Training setting
n_classes = 2
epochs = 300 
batch_size = 256
num = 10
num_workers = 7


C_total = np.zeros((n_classes, n_classes))
C = np.zeros((n_classes, n_classes))
C_new = np.zeros((n_classes, n_classes))

2025-07-22 21:06:24.103030: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-07-22 21:06:24.103067: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-07-22 21:06:24.104187: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


## LeNet + CE

In [5]:


class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
            inputs, targets,patients = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device), patients
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc,out,targets
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 

        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        count = 0

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc,out,targets =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc,out,targets= self.iterate(epoch, "test")

                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                        "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)
                    count = 1 

                    #self.scheduler.step()

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
                
        if count == 0 :
            checkpoint = {
                "epoch": epoch,
                "train_acc":train_acc,
                "test_acc":test_acc,
                "test_loss": test_loss,
                "state_dict": self.net.state_dict(),
            }
            torch.save(checkpoint, self.model_path)


        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
        

    def test_iterate(self, phase):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        
        with torch.no_grad():
            for batch_idx, (inputs, targets,patients) in enumerate(dataloader):
                inputs, targets ,patients = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda'), patients
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

            targets_combine = np.concatenate(targets_combine, axis=0) 
            patient_ids = np.concatenate( patient_ids, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
        
        return (
                np.hstack(y_pred),
                np.hstack(y_true),
                np.vstack(y_pred_prob),
                features_out,
                features_combine,
                targets_combine,
                patient_ids,
            )
    def test(self):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets,train_patient_ids = self.test_iterate("train")
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test")
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            if np.sum(idx) == 0:
                acc = 0.0  # 若該類別未出現，定義為 0
            else:
                acc = accuracy_score(y_true[idx], y_pred[idx])
            print("class", i, acc)

        from sklearn.metrics import confusion_matrix
        print(confusion_matrix(y_true, y_pred, labels=list(range(n_classes))))

        return (
            confusion_matrix(y_true, y_pred, labels=list(range(n_classes))),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            train_patient_ids,
            test_patient_ids
        )

In [6]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

# metrics
lenet_train_avg_accuracy = []
lenet_avg_accuracy = []
lenet_avg_roc = []

all_patients = df_p['Patient_ID'].unique()
num = len(all_patients)

print(f"共有 {num} 位病患，將進行 Leave-One-Patient-Out 驗證")

    
for i, test_patient in enumerate(all_patients):
    print(f"\n[LOPO Iteration {i+1}/{num}] 測試病患 ID: {test_patient}")

    test_data = df_p[df_p['Patient_ID'] == test_patient]
    train_data = df_p[df_p['Patient_ID'] != test_patient]

    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)


    dl_tr = spectral_dataloader(
                            X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                        )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = Variant_LeNet(in_channels=1, out_channels=n_classes)

    model_path = f"best_variant_lenet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    lenet_train_avg_accuracy.append(train_acc)
    lenet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"variant_lenet_best_test_accuracy_combined_train",f"variant_lenet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"variant_lenet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"variant_lenet_low_test_accuracy_combined_train",f"variant_lenet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"variant_lenet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    # metrices result
    df = pd.DataFrame(
            {
                "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
                "Recall": [
                        recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
                "Precision": [
                        precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "F1 Score": [
                        f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                }
    )
    print(df.transpose())

    C = confusion_matrix(y_true, y_pred, labels=list(range(n_classes)))
    counts = np.bincount(y_test, minlength=n_classes)

    # 安全初始化 C_new
    C_new = np.zeros_like(C)

    for k in range(n_classes):
        if counts[k] > 0:
            C_new[k] = np.round((C[k] / (counts[k] * num)), 2)

    # 正規化為 row-wise 百分比
    with np.errstate(divide='ignore', invalid='ignore'):
        cm = 100 * C_new / C_new.sum(axis=1, keepdims=True)
        cm[np.isnan(cm)] = 0  # 0/0 → NaN → 0
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"variant_lenet_{i}_roc_curve", y_true, y_test, y_pred_prob)

plot_heatmap(f"variant_lenet_average_heatmap", C_total,class_names=classnames)


共有 40 位病患，將進行 Leave-One-Patient-Out 驗證

[LOPO Iteration 1/40] 測試病患 ID: GN071
1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.424 | acc: 71.97% (2319/3222)


  0%|          | 1/300 [00:00<02:19,  2.15it/s]


epoch 1: test average loss: 1.268 | acc: 0.00% (0/79)

epoch 2: train average loss: 0.274 | acc: 82.81% (2668/3222)


...

 10%|▉         | 29/300 [00:09<01:30,  2.99it/s]


epoch 30: test average loss: 3.178 | acc: 2.00% (1/50)
EarlyStopping counter: 25/25 (best: 1.0000)
🔴 Early stopping triggered
load model at epoch 5, with test acc : 1.000



/tmp/ipykernel_2438126/1858653347.py:174: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 1.0
class 0 0.0
class 1 1.0
[[ 0  0]
 [ 0 50]]
                 0
Accuracy       1.0
Recall       [1.0]
Specificity  [0.0]
Precision    [1.0]
F1 Score     [1.0]


/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning:

Specificity is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_ranking.py:1183: UndefinedMetricWarning:

No positive samples in y_true, true positive value should be meaningless



In [9]:
print("max test acc:", np.max(lenet_avg_accuracy))
print("min test acc:", np.min(lenet_avg_accuracy))

print("train mean:", np.mean(lenet_train_avg_accuracy))
print("train std:", np.std(lenet_train_avg_accuracy))

    
print("mean:", np.mean(lenet_avg_accuracy))
print("std:", np.std(lenet_avg_accuracy))

    

max test acc: 1.0
min test acc: 0.4177215189873418
train mean: 0.9279250794533365
train std: 0.1064428834907521
mean: 0.9495807930767244
std: 0.11903157489188528


## ResNet + CE

In [12]:

from datasets_spectrum import spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

resnet_train_avg_accuracy = []
resnet_avg_accuracy = []
resnet_avg_roc = []


all_patients = df_p['Patient_ID'].unique()
num = len(all_patients)

print(f"共有 {num} 位病患，將進行 Leave-One-Patient-Out 驗證")

    
for i, test_patient in enumerate(all_patients):
    print(f"\n[LOPO Iteration {i+1}/{num}] 測試病患 ID: {test_patient}")

    test_data = df_p[df_p['Patient_ID'] == test_patient]
    train_data = df_p[df_p['Patient_ID'] != test_patient]

    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)
    
    dl_tr = spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    # setting resnet
    layers = 6
    hidden_size = 100
    block_size = 2
    hidden_sizes = [hidden_size] * layers
    num_blocks = [block_size] * layers
    input_dim = 400
    model = ResNet(
                    hidden_sizes,
                    num_blocks,
                    input_dim=input_dim,
                    in_channels=64,
                    n_classes=2,
                )

    model_path = f"best_resnet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    resnet_train_avg_accuracy.append(train_acc)
    resnet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"resnet_best_test_accuracy_combined_train",f"resnet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"resnet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"resnet_low_test_accuracy_combined_train",f"resnet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"resnet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    # metrices result
    df = pd.DataFrame(
            {
                "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
                "Recall": [
                        recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
                "Precision": [
                        precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "F1 Score": [
                        f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                }
    )
    print(df.transpose())

    C = confusion_matrix(y_true, y_pred, labels=list(range(n_classes)))
    counts = np.bincount(y_test, minlength=n_classes)

    # 安全初始化 C_new
    C_new = np.zeros_like(C)

    for k in range(n_classes):
        if counts[k] > 0:
            C_new[k] = np.round((C[k] / (counts[k] * num)), 2)

    # 正規化為 row-wise 百分比
    with np.errstate(divide='ignore', invalid='ignore'):
        cm = 100 * C_new / C_new.sum(axis=1, keepdims=True)
        cm[np.isnan(cm)] = 0  # 0/0 → NaN → 0
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"resnet_{i}_roc_curve", y_true, y_test, y_pred_prob)

plot_heatmap(f"resnet_average_heatmap", C_total,class_names=classnames)


共有 40 位病患，將進行 Leave-One-Patient-Out 驗證

[LOPO Iteration 1/40] 測試病患 ID: GN071
1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.566 | acc: 78.43% (2527/3222)


  0%|          | 1/300 [00:00<04:01,  1.24it/s]


epoch 1: test average loss: 0.950 | acc: 0.00% (0/79)

epoch 2: train average loss: 0.421 | acc: 88.45% (2850/3222)


...

 10%|▉         | 29/300 [00:18<02:48,  1.60it/s]


epoch 30: test average loss: 0.173 | acc: 94.00% (47/50)
EarlyStopping counter: 25/25 (best: 1.0000)
🔴 Early stopping triggered
load model at epoch 5, with test acc : 1.000



/tmp/ipykernel_2438126/1858653347.py:174: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 1.0
class 0 0.0
class 1 1.0
[[ 0  0]
 [ 0 50]]
                 0
Accuracy       1.0
Recall       [1.0]
Specificity  [0.0]
Precision    [1.0]
F1 Score     [1.0]


/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning:

Specificity is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_ranking.py:1183: UndefinedMetricWarning:

No positive samples in y_true, true positive value should be meaningless



In [15]:
print("max test acc:", np.max(resnet_avg_accuracy))
print("min test acc:", np.min(resnet_avg_accuracy))

print("train mean:", np.mean(resnet_train_avg_accuracy))
print("train std:", np.std(resnet_train_avg_accuracy))

    
print("mean:", np.mean(resnet_avg_accuracy))
print("std:", np.std(resnet_avg_accuracy))
    

max test acc: 1.0
min test acc: 0.9625
train mean: 0.905719211114931
train std: 0.08693333848357224
mean: 0.9986041666666667
std: 0.0061191511189597715


## RamanNet + CE

In [16]:

from datasets_sliding_window import sliding_spectral_dataloader
from sklearn.model_selection import StratifiedKFold
best_test_accuracy = 0
low_test_accuracy = 1

ramannet_train_avg_accuracy = []
ramannet_avg_accuracy = []
ramannet_avg_roc = []


all_patients = df_p['Patient_ID'].unique()
num = len(all_patients)

print(f"共有 {num} 位病患，將進行 Leave-One-Patient-Out 驗證")

    
for i, test_patient in enumerate(all_patients):
    print(f"\n[LOPO Iteration {i+1}/{num}] 測試病患 ID: {test_patient}")

    test_data = df_p[df_p['Patient_ID'] == test_patient]
    train_data = df_p[df_p['Patient_ID'] != test_patient]

    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)

    dl_tr = sliding_spectral_dataloader(
                        X_train, y_train,patient_train, idxs=None, batch_size=batch_size, shuffle=True
                    )
    dl_test = sliding_spectral_dataloader(X_test, y_test,patient_test,idxs=None, batch_size=batch_size, shuffle=False)
    values, counts = np.unique(np.asarray(y_test), return_counts=True)
    dataloaders = {"train": dl_tr, "test": dl_test}

    model = RamanNet(w_len=50, n_windows=14,n_classes=2)

    model_path = f"best_ramannet_model_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,train_patient_ids, test_patient_ids= solver.test()
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ramannet_train_avg_accuracy.append(train_acc)
    ramannet_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne_interactive_html(f"ramannet_best_test_accuracy_combined_train",f"ramannet_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets, train_patient_ids, test_patient_ids,classnames )
      
        plot_heatmap(f"ramannet_best_test_accuracy_heatmap", C,class_names=classnames)
        
    if test_accuracy < low_test_accuracy:

        low_test_accuracy = test_accuracy
        
        plot_tsne_interactive_html(f"ramannet_low_test_accuracy_combined_train",f"ramannet_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets,train_patient_ids, test_patient_ids, classnames )
            
        plot_heatmap(f"ramannet_low_test_accuracy_heatmap", C,class_names=classnames)
        
    # metrices result
    df = pd.DataFrame(
            {
                "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
                "Recall": [
                        recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
                "Precision": [
                        precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "F1 Score": [
                        f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                }
    )
    print(df.transpose())

    C = confusion_matrix(y_true, y_pred, labels=list(range(n_classes)))
    counts = np.bincount(y_test, minlength=n_classes)

    # 安全初始化 C_new
    C_new = np.zeros_like(C)

    for k in range(n_classes):
        if counts[k] > 0:
            C_new[k] = np.round((C[k] / (counts[k] * num)), 2)

    # 正規化為 row-wise 百分比
    with np.errstate(divide='ignore', invalid='ignore'):
        cm = 100 * C_new / C_new.sum(axis=1, keepdims=True)
        cm[np.isnan(cm)] = 0  # 0/0 → NaN → 0
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"ramannet_{i}_roc_curve", y_true, y_test, y_pred_prob)

plot_heatmap(f"ramannet_average_heatmap", C_total,class_names=classnames)


共有 40 位病患，將進行 Leave-One-Patient-Out 驗證

[LOPO Iteration 1/40] 測試病患 ID: GN071
1


  0%|          | 0/300 [00:00<?, ?it/s]


epoch 1: train average loss: 0.451 | acc: 71.45% (2302/3222)


  0%|          | 1/300 [00:00<02:04,  2.39it/s]


epoch 1: test average loss: 0.303 | acc: 100.00% (79/79)
best test acc found

epoch 2: train average loss: 0.236 | acc: 90.13% (2904/3222)


...

  8%|▊         | 25/300 [00:12<02:12,  2.08it/s]


epoch 26: test average loss: 5.885 | acc: 22.00% (11/50)
EarlyStopping counter: 25/25 (best: 1.0000)
🔴 Early stopping triggered
load model at epoch 1, with test acc : 1.000



/tmp/ipykernel_2438126/1858653347.py:174: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.



total 1.0
class 0 0.0
class 1 1.0
[[ 0  0]
 [ 0 50]]
                 0
Accuracy       1.0
Recall       [1.0]
Specificity  [0.0]
Precision    [1.0]
F1 Score     [1.0]


/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning:

Specificity is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.

/home/user/.local/lib/python3.10/site-packages/sklearn/metrics/_ranking.py:1183: UndefinedMetricWarning:

No positive samples in y_true, true positive value should be meaningless



In [17]:
print("max test acc:", np.max(ramannet_avg_accuracy))
print("min test acc:", np.min(ramannet_avg_accuracy))

print("train mean:", np.mean(ramannet_train_avg_accuracy))
print("train std:", np.std(ramannet_train_avg_accuracy))

    
print("mean:", np.mean(ramannet_avg_accuracy))
print("std:", np.std(ramannet_avg_accuracy))

    

max test acc: 1.0
min test acc: 0.0
train mean: 0.7808156239627937
train std: 0.09108271198784783
mean: 0.9161084739803094
std: 0.23440904453039552


## ViT+CE

In [ ]:
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion = nn.CrossEntropyLoss(weight=alpha).cuda()
        self.get_num_labeled_class = 2
        self.optimizer = optim.Adam(self.net.parameters(),lr = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets) in enumerate(dataloader):
            inputs, targets = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device)
            out,emb= self.net(inputs)
            
            loss = self.criterion(out, targets)
            
            outputs = torch.argmax(out.detach(), dim=1)
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 
        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        count = 0

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                        "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)
                    count = 1 

                    #self.scheduler.step()

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
                
        if count == 0 :
            checkpoint = {
                "epoch": epoch,
                "train_acc":train_acc,
                "test_acc":test_acc,
                "test_loss": test_loss,
                "state_dict": self.net.state_dict(),
            }
            torch.save(checkpoint, self.model_path)
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
            

    def test_iterate(self, phase,patients):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        all_patient_ids = patients
        
        with torch.no_grad():
            global_idx = 0  # 用來對應 patient ID
            for batch_idx, (inputs, targets) in enumerate(dataloader):

                inputs, targets  = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda')
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

                if phase == 'test':
                    patient_ids.extend([str(p) for p in all_patient_ids[global_idx:global_idx + batch_size]])
                    global_idx += 256


            targets_combine = np.concatenate(targets_combine, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
            print(patient_ids)

            flat_patient_ids = []

            for p in patient_ids:
                if isinstance(p, (list, np.ndarray)):
                    flat_patient_ids.extend([str(i) for i in p])
                else:
                    flat_patient_ids.append(str(p))
        if phase == 'train':
            return (
                    np.hstack(y_pred),
                    np.hstack(y_true),
                    np.vstack(y_pred_prob),
                    features_out,
                    features_combine,
                    targets_combine,
                )
        else:
            return (
                    np.hstack(y_pred),
                    np.hstack(y_true),
                    np.vstack(y_pred_prob),
                    features_out,
                    features_combine,
                    targets_combine,
                    np.array(flat_patient_ids, dtype=str) 
                )


    def test(self,patient_idx):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets = self.test_iterate("train",patient_idx)
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test",patient_idx)
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            if np.sum(idx) == 0:
                acc = 0.0  # 若該類別未出現，定義為 0
            else:
                acc = accuracy_score(y_true[idx], y_pred[idx])
            print("class", i, acc)

        from sklearn.metrics import confusion_matrix
        print(confusion_matrix(y_true, y_pred, labels=[0, 1]))


        return (
            confusion_matrix(y_true, y_pred, labels=list(range(self.n_classes))),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            test_patient_ids
        )

In [27]:
from sklearn.model_selection import StratifiedKFold
import torch.utils.data as Data
from plot import plot_tsne
best_test_accuracy = 0
low_test_accuracy = 1

ViT_train_avg_accuracy = []
ViT_avg_accuracy = []
ViT_avg_roc = []


all_patients = df_p['Patient_ID'].unique()
num = len(all_patients)

print(f"共有 {num} 位病患，將進行 Leave-One-Patient-Out 驗證")

    
for i, test_patient in enumerate(all_patients):
    print(f"\n[LOPO Iteration {i+1}/{num}] 測試病患 ID: {test_patient}")

    test_data = df_p[df_p['Patient_ID'] == test_patient]
    train_data = df_p[df_p['Patient_ID'] != test_patient]

    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)
    
    # Set up dataloaders
    X_train = torch.from_numpy(X_train.astype(np.float32))
    y_train = torch.from_numpy(y_train.astype(np.longlong))


    if isinstance(X_test, np.ndarray):
        X_test = torch.from_numpy(X_test).float()
    else:
        X_test = X_test.float()  # 如果 X_test 已經是張量

    if isinstance(y_test, np.ndarray):
        y_test = torch.from_numpy(y_test).long()
    else:
        y_test = y_test.long()  # 如果 y_test 已經是張量


    dataset_tr = Data.TensorDataset(X_train, y_train)
    dl_tr = Data.DataLoader(dataset_tr, batch_size=batch_size, shuffle = True)
        
        
    dataset_test = Data.TensorDataset(X_test, y_test)
    dl_test = Data.DataLoader(dataset_test, batch_size=batch_size, shuffle = False)
    
    patient_ids = patient_test.values.tolist()  # list of string IDs, index aligned with dataset_test

    values, counts = np.unique(np.asarray(y_test), return_counts=True)

    dataloaders = {"train": dl_tr, "test": dl_test}

    model = ViT(image_size = (1,400), patch_size = (1, 16), num_classes = n_classes, channels = 1, dim = 64, depth = 3, heads = 6, mlp_dim = 128, dropout = 0.1, emb_dropout = 0.1)

    model_path = f"best_ViT_{i}.pth"

    
    labels = np.array(y_train)  # y_train是所有訓練樣本的標籤

    n_samples = len(labels)
    n_classes = len(np.unique(labels))
    class_sample_count = np.array([(labels == t).sum() for t in range(n_classes)])

    class_weights = n_samples / (n_classes * class_sample_count)
    class_weights = torch.tensor(class_weights, dtype=torch.float32).cuda()
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,test_patient_ids= solver.test(patient_ids)
    C_total += C  # 將每次迭代的 C 加總到 C_total
    ViT_train_avg_accuracy.append(train_acc)
    ViT_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne(f"best_test_accuracy_combined_train",f"best_test_accuracy_combined_test",train_combined,combined,train_targets,targets,classnames )
        
        plot_heatmap(f"finetune_best_test_accuracy_heatmap", C,class_names=classnames)
    
    if test_accuracy < low_test_accuracy:
            
        low_test_accuracy = test_accuracy
        plot_tsne(f"low_test_accuracy_combined_train",f"low_test_accuracy_combined_test",train_combined,combined,train_targets,targets, classnames )
        
        plot_heatmap(f"finetune_low_test_accuracy_heatmap", C,class_names=classnames)
        
    # metrices result
    df = pd.DataFrame(
            {
                "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
                "Recall": [
                        recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
                "Precision": [
                        precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "F1 Score": [
                        f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                }
    )
    print(df.transpose())

    C = confusion_matrix(y_true, y_pred, labels=list(range(n_classes)))
    counts = np.bincount(y_test, minlength=n_classes)

    # 安全初始化 C_new
    C_new = np.zeros_like(C)

    for k in range(n_classes):
        if counts[k] > 0:
            C_new[k] = np.round((C[k] / (counts[k] * num)), 2)

    # 正規化為 row-wise 百分比
    with np.errstate(divide='ignore', invalid='ignore'):
        cm = 100 * C_new / C_new.sum(axis=1, keepdims=True)
        cm[np.isnan(cm)] = 0  # 0/0 → NaN → 0
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"vit_{i}_roc_curve", y_true, y_test, y_pred_prob)

plot_heatmap(f"vit_average_heatmap", C_total,class_names=classnames)


共有 40 位病患，將進行 Leave-One-Patient-Out 驗證

[LOPO Iteration 1/40] 測試病患 ID: GN071
1


  0%|          | 1/300 [00:00<00:37,  8.08it/s]


epoch 1: train average loss: 0.688 | acc: 65.80% (2120/3222)

epoch 1: test average loss: 0.721 | acc: 41.77% (33/79)
best test acc found


  1%|          | 2/300 [00:00<00:35,  8.40it/s]


epoch 2: train average loss: 0.621 | acc: 78.18% (2519/3222)

epoch 2: test average loss: 1.108 | acc: 18.99% (15/79)
EarlyStopping counter: 1/25 (best: 0.4177)


...


epoch 26: test average loss: 2.098 | acc: 22.00% (11/50)
EarlyStopping counter: 21/25 (best: 0.9600)

epoch 27: train average loss: 0.104 | acc: 96.65% (3142/3251)

epoch 27: test average loss: 4.244 | acc: 2.00% (1/50)
EarlyStopping counter: 22/25 (best: 0.9600)

epoch 28: train average loss: 0.136 | acc: 94.00% (3056/3251)


 10%|▉         | 29/300 [00:03<00:27,  9.87it/s]


epoch 28: test average loss: 2.985 | acc: 8.00% (4/50)
EarlyStopping counter: 23/25 (best: 0.9600)

epoch 29: train average loss: 0.100 | acc: 96.16% (3126/3251)

epoch 29: test average loss: 2.434 | acc: 22.00% (11/50)
EarlyStopping counter: 24/25 (best: 0.9600)

epoch 30: train average loss: 0.079 | acc: 96.95% (3152/3251)


 10%|▉         | 29/300 [00:03<00:31,  8.66it/s]
/tmp/ipykernel_2438126/995090431.py:200: FutureWarning:

You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.

/home/user/.local/lib/python3.10/site


epoch 30: test average loss: 3.802 | acc: 12.00% (6/50)
EarlyStopping counter: 25/25 (best: 0.9600)
🔴 Early stopping triggered
load model at epoch 5, with test acc : 0.960
[['X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233'], ['X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233'], ['X233', 'X233', 'X233

In [29]:
print("max test acc:", np.max(ViT_avg_accuracy))
print("min test acc:", np.min(ViT_avg_accuracy))

print("train mean:", np.mean(ViT_train_avg_accuracy))
print("train std:", np.std(ViT_train_avg_accuracy))

    
print("mean:", np.mean(ViT_avg_accuracy))
print("std:", np.std(ViT_avg_accuracy))

    


max test acc: 1.0
min test acc: 0.08
train mean: 0.7764754049691456
train std: 0.1627725281908369
mean: 0.9232304224432388
std: 0.20477920619765372


## ViT + MAPA + Focal

In [5]:
from losses import MultiAdaptiveProxyAnchorLoss
class Solver:
    def __init__(
        self,
        i,
        dataloaders,
        model,
        model_path,
        device,
        n_classes,
        alpha,
        gpu=-1,
    ):
        self.i = i
        self.dataloaders = dataloaders
        self.device = device
        self.net = model
        self.net = self.net.to(self.device)
        self.n_classes = n_classes
        self.criterion_proxy =MultiAdaptiveProxyAnchorLoss(nb_classes=n_classes, sz_embed=256, mrg=0.5, alpha=32,\
                                             nb_proxies=2).cuda()
        self.criterion = FocalLoss(alpha=alpha, gamma=2).cuda()
        self.get_num_labeled_class = 2
        self.param_groups = [
            {'params': list(set(model.parameters()).difference(set(model.embedding.parameters())))},
            {'params': model.embedding.parameters() , 'lr':float(0.001) * 1},
            {'params': self.criterion_proxy.mrg,'lr':float(0.001) },
            {'params': self.criterion_proxy.proxies, 'lr':float(0.001) * 100}
        ]
        self.optimizer =torch.optim.AdamW(self.param_groups, lr=0.001, weight_decay = 0.001)
        self.model_path = model_path


    def iterate(self, epoch, phase):
        if phase == "train":
            self.net.train()
        else:
            self.net.eval()

            
        dataloader = self.dataloaders[phase]
        total_loss = 0
        correct = 0
        total = 0
            
        for batch_idx, (inputs, targets) in enumerate(dataloader):
            inputs, targets = Variable(inputs).to(self.device), Variable(targets.long()).to(self.device)
            out,emb= self.net(inputs)
            
            loss1 = self.criterion(out, targets)
            loss2 = self.criterion_proxy(emb, targets)
            loss = loss1 + 0.5 * loss2
            outputs = torch.argmax(out.detach(), dim=1)
            
            
            if phase == "train":
                self.optimizer.zero_grad()
                loss.backward()
                self.optimizer.step()
                torch.nn.utils.clip_grad_value_(self.net.parameters(), 10)
                torch.nn.utils.clip_grad_value_(self.criterion_proxy.parameters(), 10)


            total_loss += loss.item()
            total += targets.size(0)
            correct += outputs.eq(targets).cpu().sum().item()

        total_loss /= (batch_idx + 1)
        total_acc = correct / total

                
        print("\nepoch %d: %s average loss: %.3f | acc: %.2f%% (%d/%d)"
                % (epoch + 1, phase, total_loss, 100.0 * total_acc, correct, total))

        return total_loss,total_acc
            

    def train(self, epochs):
        best_loss = float("inf")
        best_acc = 0
        epoch_breaks_classifer = 0
        train_losses = []
        train_acces = [] 
        test_losses = []
        test_acces = [] 
        early_stopping_classifier = EarlyStopping(patience=25, mode='acc', verbose=True)

        count = 0

        for epoch in tqdm(range(epochs)):
            train_loss,train_acc =self.iterate(epoch, "train")

            train_losses.append(train_loss)
            train_acces.append(train_acc)

            with torch.no_grad():
                
                test_loss,test_acc= self.iterate(epoch, "test")
                    
                test_losses.append(test_loss)
                test_acces.append(test_acc)

                

                if test_acc > best_acc:
                    best_acc = test_acc
                    checkpoint = {
                        "epoch": epoch,
                        "train_acc":train_acc,
                        "test_acc":test_acc,
                        "test_loss": test_loss,
                        "state_dict": self.net.state_dict(),
                    }
                    print("best test acc found")
                    torch.save(checkpoint, self.model_path)
                    count = 1 

                    #self.scheduler.step()

                early_stopping_classifier(test_acc)

                epoch_breaks_classifer+= 1

                if early_stopping_classifier.early_stop:
                    break  # 停止訓練
                
        if count == 0 :
            checkpoint = {
                "epoch": epoch,
                "train_acc":train_acc,
                "test_acc":test_acc,
                "test_loss": test_loss,
                "state_dict": self.net.state_dict(),
            }
            torch.save(checkpoint, self.model_path)
        
        if not early_stopping_classifier.early_stop:
            epoch_breaks_classifer = epochs
            

    def test_iterate(self, phase,patients):
        self.net.eval()
        dataloader = self.dataloaders[phase]
        y_pred = []
        y_true = []
        y_pred_prob = []
        
        features_out = []
        features_combine = []
        targets_combine = []
        patient_ids = []
        all_patient_ids = patients
        
        with torch.no_grad():
            global_idx = 0  # 用來對應 patient ID
            for batch_idx, (inputs, targets) in enumerate(dataloader):

                inputs = inputs.reshape((inputs.shape[0],1, 1, -1))

                inputs, targets  = Variable(inputs).to('cuda'), Variable(targets.long()).to('cuda')
                out,emb = self.net(inputs)
                outputs = torch.argmax(out.detach(), dim=1)
                outputs_prob = nn.functional.softmax(out.detach(), dim=1)
                y_pred.append(outputs.cpu().numpy())
                y_pred_prob.append(outputs_prob.cpu().numpy())
            
                y_true.append(targets.cpu().numpy())
                
                targets_combine.append(targets.detach().cpu().numpy())
                patient_ids.append(patients)
                features_out.append(out.cpu().numpy())
                features_combine.append(emb.detach().cpu().numpy())

                if phase == 'test':
                    patient_ids.extend([str(p) for p in all_patient_ids[global_idx:global_idx + batch_size]])
                    global_idx += 256


            targets_combine = np.concatenate(targets_combine, axis=0) 
            features_out = np.concatenate(features_out, axis=0)
            features_combine = np.concatenate(features_combine, axis=0)
            print(patient_ids)

            flat_patient_ids = []

            for p in patient_ids:
                if isinstance(p, (list, np.ndarray)):
                    flat_patient_ids.extend([str(i) for i in p])
                else:
                    flat_patient_ids.append(str(p))
        if phase == 'train':
            return (
                    np.hstack(y_pred),
                    np.hstack(y_true),
                    np.vstack(y_pred_prob),
                    features_out,
                    features_combine,
                    targets_combine,
                )
        else:
            return (
                    np.hstack(y_pred),
                    np.hstack(y_true),
                    np.vstack(y_pred_prob),
                    features_out,
                    features_combine,
                    targets_combine,
                    np.array(flat_patient_ids, dtype=str) 
                )


    def test(self,patient_idx):
        checkpoint = torch.load(self.model_path)
        epoch = checkpoint["epoch"]
        train_acc = checkpoint["train_acc"]
        test_acc = checkpoint["test_acc"]
        self.net.load_state_dict(checkpoint["state_dict"])
        print("load model at epoch {}, with test acc : {:.3f}".format(epoch+1, test_acc))

        
        _, _ ,_,train_out,train_combined,train_targets = self.test_iterate("train",patient_idx)
        y_pred, y_true ,y_pred_prob,out,combined,targets, test_patient_ids,= self.test_iterate("test",patient_idx)
        
        print("total", accuracy_score(y_true, y_pred))
        for i in range(self.n_classes):
            idx = y_true == i
            if np.sum(idx) == 0:
                acc = 0.0  # 若該類別未出現，定義為 0
            else:
                acc = accuracy_score(y_true[idx], y_pred[idx])
            print("class", i, acc)

        from sklearn.metrics import confusion_matrix
        print(confusion_matrix(y_true, y_pred, labels=[0, 1]))


        return (
            confusion_matrix(y_true, y_pred, labels=list(range(self.n_classes))),
            y_true,
            y_pred,
            accuracy_score(y_true, y_pred),
            y_pred_prob,
            train_acc,
            train_targets,
            targets,
            train_combined,
            combined,
            test_patient_ids
        )

In [6]:
from sklearn.model_selection import StratifiedKFold
import torch.utils.data as Data
from plot import plot_tsne
best_test_accuracy = 0
low_test_accuracy = 1

vit_mapa_focal_train_avg_accuracy = []
vit_mapa_focal_avg_accuracy = []
vit_mapa_focal_avg_roc = []


all_patients = df_p['Patient_ID'].unique()
num = len(all_patients)

print(f"共有 {num} 位病患，將進行 Leave-One-Patient-Out 驗證")

    
for i, test_patient in enumerate(all_patients):
    print(f"\n[LOPO Iteration {i+1}/{num}] 測試病患 ID: {test_patient}")

    test_data = df_p[df_p['Patient_ID'] == test_patient]
    train_data = df_p[df_p['Patient_ID'] != test_patient]

    train_data.reset_index(drop=True, inplace=True)
    test_data.reset_index(drop=True, inplace=True)

    X_train, X_test = train_data.iloc[:, :-2].values , test_data.iloc[:, :-2].values
    y_train, y_test = train_data['Classes'], test_data['Classes']
    patient_train,patient_test  = train_data['Patient_ID'],test_data['Patient_ID']

    y_train = y_train.values.astype(int)
    y_test = y_test.values.astype(int)
    
    # Set up dataloaders
    X_train = torch.from_numpy(X_train.astype(np.float32))
    y_train = torch.from_numpy(y_train.astype(np.longlong))


    if isinstance(X_test, np.ndarray):
        X_test = torch.from_numpy(X_test).float()
    else:
        X_test = X_test.float()  # 如果 X_test 已經是張量

    if isinstance(y_test, np.ndarray):
        y_test = torch.from_numpy(y_test).long()
    else:
        y_test = y_test.long()  # 如果 y_test 已經是張量


    dataset_tr = Data.TensorDataset(X_train, y_train)
    dl_tr = Data.DataLoader(dataset_tr, batch_size=batch_size, shuffle = True)
        
        
    dataset_test = Data.TensorDataset(X_test, y_test)
    dl_test = Data.DataLoader(dataset_test, batch_size=batch_size, shuffle = False)
    
    patient_ids = patient_test.values.tolist()  # list of string IDs, index aligned with dataset_test

    values, counts = np.unique(np.asarray(y_test), return_counts=True)

    dataloaders = {"train": dl_tr, "test": dl_test}

    model = ViT(image_size = (1,400), patch_size = (1, 16), num_classes = n_classes, channels = 1, dim = 64, depth = 3, heads = 6, mlp_dim = 128, dropout = 0.1, emb_dropout = 0.1)

    model_path = f"best_vit_mapa_focal_{i}.pth"

    
    class_counts = np.bincount(y_train)
    num_classes = len(class_counts)
    total_samples = len(y_train)

    class_weights = []
    for count in class_counts:
        weight = 1 / (count / total_samples)
        class_weights.append(weight)
    class_weights = torch.FloatTensor(class_weights)
    alpha = class_weights
    solver = Solver(
                i,dataloaders, model, model_path, 'cuda', n_classes, alpha
            )
    print(i + 1)
    solver.train(epochs)
    C, y_true, y_pred, test_accuracy , y_pred_prob,train_acc,train_targets,targets,train_combined,combined ,test_patient_ids= solver.test(patient_ids)
    C_total += C  # 將每次迭代的 C 加總到 C_total
    vit_mapa_focal_train_avg_accuracy.append(train_acc)
    vit_mapa_focal_avg_accuracy.append(test_accuracy)

    if test_accuracy > best_test_accuracy:

        best_test_accuracy = test_accuracy
            
        plot_tsne(f"vit_mapa_focal_best_test_accuracy_combined_train",f"vit_mapa_focal_best_test_accuracy_combined_test",train_combined,combined,train_targets,targets,classnames )
        
        plot_heatmap(f"vit_mapa_focal_best_test_accuracy_heatmap", C,class_names=classnames)
    
    if test_accuracy < low_test_accuracy:
            
        low_test_accuracy = test_accuracy
        plot_tsne(f"vit_mapa_focal_low_test_accuracy_combined_train",f"vit_mapa_focal_low_test_accuracy_combined_test",train_combined,combined,train_targets,targets, classnames )
        
        plot_heatmap(f"vit_mapa_focal_low_test_accuracy_heatmap", C,class_names=classnames)
        
    # metrices result
    df = pd.DataFrame(
            {
                "Accuracy": [np.round(accuracy_score(y_true, y_pred), 4)],
                "Recall": [
                        recall_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "Specificity": [specificity_score(y_true, y_pred, average=None).round(4)],
                "Precision": [
                        precision_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                "F1 Score": [
                        f1_score(y_true, y_pred, average=None, zero_division=0).round(4)
                    ],
                }
    )
    print(df.transpose())

    C = confusion_matrix(y_true, y_pred, labels=list(range(n_classes)))
    counts = np.bincount(y_test, minlength=n_classes)

    # 安全初始化 C_new
    C_new = np.zeros_like(C)

    for k in range(n_classes):
        if counts[k] > 0:
            C_new[k] = np.round((C[k] / (counts[k] * num)), 2)

    # 正規化為 row-wise 百分比
    with np.errstate(divide='ignore', invalid='ignore'):
        cm = 100 * C_new / C_new.sum(axis=1, keepdims=True)
        cm[np.isnan(cm)] = 0  # 0/0 → NaN → 0
    sns.set_context("talk", rc={"font": "Helvetica", "font.size": 12})
    label = [STRAINS[i] for i in ORDER]

    plot_CR_K_pneumonia_CS_K_pneumonia_ROC_curve(f"vit_mapa_focal_{i}_roc_curve", y_true, y_test, y_pred_prob)

plot_heatmap(f"vit_mapa_focal_average_heatmap", C_total,class_names=classnames)


共有 40 位病患，將進行 Leave-One-Patient-Out 驗證

[LOPO Iteration 1/40] 測試病患 ID: GN071
1


  0%|          | 1/300 [00:00<02:05,  2.39it/s]


epoch 1: train average loss: 27.245 | acc: 18.84% (607/3222)

epoch 1: test average loss: 3.994 | acc: 100.00% (79/79)
best test acc found


  1%|          | 2/300 [00:00<01:28,  3.35it/s]


epoch 2: train average loss: 22.191 | acc: 83.83% (2701/3222)

epoch 2: test average loss: 1.248 | acc: 0.00% (0/79)
EarlyStopping counter: 1/25 (best: 1.0000)


...

  8%|▊         | 25/300 [00:05<01:03,  4.30it/s]


epoch 25: train average loss: 11.098 | acc: 93.94% (3054/3251)

epoch 25: test average loss: 2.586 | acc: 58.00% (29/50)
EarlyStopping counter: 24/25 (best: 1.0000)


  8%|▊         | 25/300 [00:05<01:05,  4.21it/s]


epoch 26: train average loss: 10.702 | acc: 95.29% (3098/3251)

epoch 26: test average loss: 3.445 | acc: 42.00% (21/50)
EarlyStopping counter: 25/25 (best: 1.0000)
🔴 Early stopping triggered
load model at epoch 1, with test acc : 1.000
[['X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233'], ['X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233', 'X233'


/tmp/ipykernel_3594140/810254962.py:213: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(self.model_path)
/home/user/.local/lib/python3.10/site-packag

In [42]:
print("max test acc:", np.max(vit_mapa_focal_avg_accuracy))
print("min test acc:", np.min(vit_mapa_focal_avg_accuracy))

print("train mean:", np.mean(vit_mapa_focal_train_avg_accuracy))
print("train std:", np.std(vit_mapa_focal_train_avg_accuracy))

    
print("mean:", np.mean(vit_mapa_focal_avg_accuracy))
print("std:", np.std(vit_mapa_focal_avg_accuracy))



max test acc: 1.0
min test acc: 1.0
train mean: 0.4457681962730235
train std: 0.15404377985597073
mean: 1.0
std: 0.0


In [43]:
import numpy as np

# 將模型名稱與對應數據組成字典，便於迴圈處理
models = {
    "ViT + MAPA + Focal": vit_mapa_focal_avg_accuracy,
    "RamanNet + CE": ramannet_avg_accuracy,
    "LeNet + CE": lenet_avg_accuracy,
    "ResNet + CE": resnet_avg_accuracy,
    "ViT + CE": ViT_avg_accuracy
}

# 輸出結果
print("Model Comparison (Mean ± Std):")
for name, acc in models.items():
    mean_acc = np.mean(acc)
    std_acc = np.std(acc)
    print(f"{name:<20}: {mean_acc:.4f} ± {std_acc:.4f}")


Model Comparison (Mean ± Std):
ViT + MAPA + Focal  : 1.0000 ± 0.0000
RamanNet + CE       : 0.9161 ± 0.2344
LeNet + CE          : 0.9496 ± 0.1190
ResNet + CE         : 0.9986 ± 0.0061
ViT + CE            : 0.9232 ± 0.2048
